In [60]:
import pandas as pd
import os
from pathlib import Path
import plotly.graph_objects as go
import plotly.express as px
import seaborn as sns
import matplotlib.pyplot as plt
import json
import predict_energy_behavior.data.read
import predict_energy_behavior.data.constants
import predict_energy_behavior.features
import numpy as np

%load_ext autoreload
%autoreload 2

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [61]:
PATH_REPO_ROOT = Path().resolve().parent
PATH_DATA = PATH_REPO_ROOT / "data"
PATH_DATA_RAW = PATH_DATA / "raw"
PATH_DATA_RAW

PosixPath('/beegfs/.global0/ws/s4610340-energy_behavior/yahor/kaggle-predict_energy_behavior_of_prosumers/data/raw')

In [62]:
raw_datasets = predict_energy_behavior.data.read.read_datasets_from_folder(PATH_DATA_RAW)
raw_datasets.__dataclass_fields__

{'data': Field(name='data',type=<class 'polars.dataframe.frame.DataFrame'>,default=<dataclasses._MISSING_TYPE object at 0x7fbbba7373d0>,default_factory=<dataclasses._MISSING_TYPE object at 0x7fbbba7373d0>,init=True,repr=True,hash=None,compare=True,metadata=mappingproxy({}),kw_only=False,_field_type=_FIELD),
 'client': Field(name='client',type=<class 'polars.dataframe.frame.DataFrame'>,default=<dataclasses._MISSING_TYPE object at 0x7fbbba7373d0>,default_factory=<dataclasses._MISSING_TYPE object at 0x7fbbba7373d0>,init=True,repr=True,hash=None,compare=True,metadata=mappingproxy({}),kw_only=False,_field_type=_FIELD),
 'gas': Field(name='gas',type=<class 'polars.dataframe.frame.DataFrame'>,default=<dataclasses._MISSING_TYPE object at 0x7fbbba7373d0>,default_factory=<dataclasses._MISSING_TYPE object at 0x7fbbba7373d0>,init=True,repr=True,hash=None,compare=True,metadata=mappingproxy({}),kw_only=False,_field_type=_FIELD),
 'electricity': Field(name='electricity',type=<class 'polars.dataframe.

In [63]:
with open(PATH_DATA_RAW / "county_id_to_name_map.json", "r") as f:
    county_id_to_name = json.load(f)

county_id_to_name 

{'0': 'HARJUMAA',
 '1': 'HIIUMAA',
 '2': 'IDA-VIRUMAA',
 '3': 'JÄRVAMAA',
 '4': 'JÕGEVAMAA',
 '5': 'LÄÄNE-VIRUMAA',
 '6': 'LÄÄNEMAA',
 '7': 'PÄRNUMAA',
 '8': 'PÕLVAMAA',
 '9': 'RAPLAMAA',
 '10': 'SAAREMAA',
 '11': 'TARTUMAA',
 '12': 'UNKNOWN',
 '13': 'VALGAMAA',
 '14': 'VILJANDIMAA',
 '15': 'VÕRUMAA'}

In [64]:
df_train = raw_datasets.data.to_pandas() 
df_train = df_train.loc[df_train["is_consumption"]==0].copy()
df_train["county_name"] = df_train["county"].astype(str).map(county_id_to_name)
df_train["product_name"] = df_train["product_type"].astype(int).map(predict_energy_behavior.data.constants.product_type_to_name)
df_train


county  is_business  product_type  target  is_consumption  \
0             0            0             1   0.713               0   
2             0            0             2   0.000               0   
4             0            0             3   2.904               0   
6             0            1             0   0.000               0   
8             0            1             1   0.000               0   
...         ...          ...           ...     ...             ...   
2018342      15            0             1   0.004               0   
2018344      15            0             3   2.287               0   
2018346      15            1             0   0.000               0   
2018348      15            1             1   0.000               0   
2018350      15            1             3   0.000               0   

                   datetime   row_id county_name     product_name  
0       2021-09-01 00:00:00        0    HARJUMAA            Fixed  
2       2021-09-01 00:00:00        2    HARJUMAA  General service  
4       2021-09-01 00:00:00        4    HARJUMAA             Spot  
6       2021-09-01 00:00:00        6    HARJUMAA         Combined  
8       2021-09-01 00:00:00        8    HARJUMAA            Fixed  
...                     ...      ...         ...              ...  
2018342 2023-05-31 23:00:00  2018342     VÕRUMAA            Fixed  
2018344 2023-05-31 23:00:00  2018344     VÕRUMAA             Spot  
2018346 2023-05-31 23:00:00  2018346     VÕRUMAA         Combined  
2018348 2023-05-31 23:00:00  2018348     VÕRUMAA            Fixed  
2018350 2023-05-31 23:00:00  2018350     VÕRUMAA             Spot  

[1009176 rows x 9 columns]

In [65]:
df_client = raw_datasets.client.to_pandas()
df_client["county_name"] = df_client["county"].astype(str).map(county_id_to_name)
df_client["product_name"] = df_client["product_type"].astype(int).map(predict_energy_behavior.data.constants.product_type_to_name)
df_client["date"] = pd.to_datetime(df_client["date"]) + pd.Timedelta(days=2)

df_client

product_type  county  eic_count  installed_capacity  is_business  \
0                 1       0        108              952.89            0   
1                 2       0         17              166.40            0   
2                 3       0        688             7207.88            0   
3                 0       0          5              400.00            1   
4                 1       0         43             1411.00            1   
...             ...     ...        ...                 ...          ...   
41914             1      15         51              415.60            0   
41915             3      15        161             2035.75            0   
41916             0      15         15              620.00            1   
41917             1      15         20              624.50            1   
41918             3      15         55             2188.20            1   

            date county_name     product_name  
0     2021-09-03    HARJUMAA            Fixed  
1     2021-09-03    HARJUMAA  General service  
2     2021-09-03    HARJUMAA             Spot  
3     2021-09-03    HARJUMAA         Combined  
4     2021-09-03    HARJUMAA            Fixed  
...          ...         ...              ...  
41914 2023-05-31     VÕRUMAA            Fixed  
41915 2023-05-31     VÕRUMAA             Spot  
41916 2023-05-31     VÕRUMAA         Combined  
41917 2023-05-31     VÕRUMAA            Fixed  
41918 2023-05-31     VÕRUMAA             Spot  

[41919 rows x 8 columns]

In [66]:
df_train_merged_with_client = predict_energy_behavior.features.process.merge_train_with_client(df_train, df_client)
df_train_merged_with_client

target  \
county product_type is_business county_name product_name    date                 
0      1            0           HARJUMAA    Fixed           2021-09-01   0.713   
       2            0           HARJUMAA    General service 2021-09-01   0.000   
       3            0           HARJUMAA    Spot            2021-09-01   2.904   
       0            1           HARJUMAA    Combined        2021-09-01   0.000   
       1            1           HARJUMAA    Fixed           2021-09-01   0.000   
...                                                                        ...   
15     1            0           VÕRUMAA     Fixed           2023-05-31   0.004   
       3            0           VÕRUMAA     Spot            2023-05-31   2.287   
       0            1           VÕRUMAA     Combined        2023-05-31   0.000   
       1            1           VÕRUMAA     Fixed           2023-05-31   0.000   
       3            1           VÕRUMAA     Spot            2023-05-31   0.000   

                                                                        is_consumption  \
county product_type is_business county_name product_name    date                         
0      1            0           HARJUMAA    Fixed           2021-09-01               0   
       2            0           HARJUMAA    General service 2021-09-01               0   
       3            0           HARJUMAA    Spot            2021-09-01               0   
       0            1           HARJUMAA    Combined        2021-09-01               0   
       1            1           HARJUMAA    Fixed           2021-09-01               0   
...                                                                                ...   
15     1            0           VÕRUMAA     Fixed           2023-05-31               0   
       3            0           VÕRUMAA     Spot            2023-05-31               0   
       0            1           VÕRUMAA     Combined        2023-05-31               0   
       1            1           VÕRUMAA     Fixed           2023-05-31               0   
       3            1           VÕRUMAA     Spot            2023-05-31               0   

                                                                                  datetime  \
county product_type is_business county_name product_name    date                             
0      1            0           HARJUMAA    Fixed           2021-09-01 2021-09-01 00:00:00   
       2            0           HARJUMAA    General service 2021-09-01 2021-09-01 00:00:00   
       3            0           HARJUMAA    Spot            2021-09-01 2021-09-01 00:00:00   
       0            1           HARJUMAA    Combined        2021-09-01 2021-09-01 00:00:00   
       1            1           HARJUMAA    Fixed           2021-09-01 2021-09-01 00:00:00   
...                                                                                    ...   
15     1            0           VÕRUMAA     Fixed           2023-05-31 2023-05-31 23:00:00   
       3            0           VÕRUMAA     Spot            2023-05-31 2023-05-31 23:00:00   
       0            1           VÕRUMAA     Combined        2023-05-31 2023-05-31 23:00:00   
       1            1           VÕRUMAA     Fixed           2023-05-31 2023-05-31 23:00:00   
       3            1           VÕRUMAA     Spot            2023-05-31 2023-05-31 23:00:00   

                                                                         row_id  \
county product_type is_business county_name product_name    date                  
0      1            0           HARJUMAA    Fixed           2021-09-01        0   
       2            0           HARJUMAA    General service 2021-09-01        2   
       3            0           HARJUMAA    Spot            2021-09-01        4   
       0            1           HARJUMAA    Combined        2021-09-01        6   
       1            1           HARJUMAA    Fixed           2021-09-01        8   
...                           

In [67]:
df_train_merged_with_client.loc[df_train_merged_with_client["installed_capacity"].isna()]

target  \
county product_type is_business county_name product_name    date                 
0      1            0           HARJUMAA    Fixed           2021-09-01   0.713   
       2            0           HARJUMAA    General service 2021-09-01   0.000   
       3            0           HARJUMAA    Spot            2021-09-01   2.904   
       0            1           HARJUMAA    Combined        2021-09-01   0.000   
       1            1           HARJUMAA    Fixed           2021-09-01   0.000   
...                                                                        ...   
10     2            1           SAAREMAA    General service 2023-05-06   0.368   
                                                            2023-05-06   0.030   
                                                            2023-05-06   0.000   
                                                            2023-05-06   0.000   
                                                            2023-05-06   0.000   

                                                                        is_consumption  \
county product_type is_business county_name product_name    date                         
0      1            0           HARJUMAA    Fixed           2021-09-01               0   
       2            0           HARJUMAA    General service 2021-09-01               0   
       3            0           HARJUMAA    Spot            2021-09-01               0   
       0            1           HARJUMAA    Combined        2021-09-01               0   
       1            1           HARJUMAA    Fixed           2021-09-01               0   
...                                                                                ...   
10     2            1           SAAREMAA    General service 2023-05-06               0   
                                                            2023-05-06               0   
                                                            2023-05-06               0   
                                                            2023-05-06               0   
                                                            2023-05-06               0   

                                                                                  datetime  \
county product_type is_business county_name product_name    date                             
0      1            0           HARJUMAA    Fixed           2021-09-01 2021-09-01 00:00:00   
       2            0           HARJUMAA    General service 2021-09-01 2021-09-01 00:00:00   
       3            0           HARJUMAA    Spot            2021-09-01 2021-09-01 00:00:00   
       0            1           HARJUMAA    Combined        2021-09-01 2021-09-01 00:00:00   
       1            1           HARJUMAA    Fixed           2021-09-01 2021-09-01 00:00:00   
...                                                                                    ...   
10     2            1           SAAREMAA    General service 2023-05-06 2023-05-06 19:00:00   
                                                            2023-05-06 2023-05-06 20:00:00   
                                                            2023-05-06 2023-05-06 21:00:00   
                                                            2023-05-06 2023-05-06 22:00:00   
                                                            2023-05-06 2023-05-06 23:00:00   

                                                                         row_id  \
county product_type is_business county_name product_name    date                  
0      1            0           HARJUMAA    Fixed           2021-09-01        0   
       2            0           HARJUMAA    General service 2021-09-01        2   
       3            0           HARJUMAA    Spot            2021-09-01        4   
       0            1           HARJUMAA    Combined        2021-09-01        6   
       1            1           HARJUMAA    Fixed           2021-09-01        8   
...                           

In [68]:
df_weather_hist = pd.read_csv(PATH_DATA_RAW / "historical_weather.csv")
df_weather_hist["datetime"] = pd.to_datetime(df_weather_hist["datetime"])
df_station_to_county = pd.read_csv(PATH_DATA_RAW / "weather_station_to_county_mapping.csv").dropna()
df_weather_naive = (
    df_weather_hist
    .set_index(["latitude", "longitude"])
    .join(df_station_to_county.set_index(["latitude", "longitude"]), on=["latitude", "longitude"])
    .dropna()
    .groupby(["county_name", "datetime"])
    .mean()
    .reset_index()
)
df_weather_naive

county_name            datetime  temperature  dewpoint  rain  snowfall  \
0         Pärnumaa 2021-09-01 00:00:00        11.15      9.85  0.00       0.0   
1         Pärnumaa 2021-09-01 01:00:00        11.10      9.95  0.00       0.0   
2         Pärnumaa 2021-09-01 02:00:00        11.20     10.05  0.00       0.0   
3         Pärnumaa 2021-09-01 03:00:00        11.45     10.20  0.00       0.0   
4         Pärnumaa 2021-09-01 04:00:00        11.45     10.15  0.00       0.0   
...            ...                 ...          ...       ...   ...       ...   
106920     Võrumaa 2023-05-30 06:00:00        10.38      3.50  0.00       0.0   
106921     Võrumaa 2023-05-30 07:00:00        11.28      2.82  0.00       0.0   
106922     Võrumaa 2023-05-30 08:00:00        12.48      2.46  0.00       0.0   
106923     Võrumaa 2023-05-30 09:00:00        12.98      3.58  0.00       0.0   
106924     Võrumaa 2023-05-30 10:00:00        13.88      3.04  0.04       0.0   

        surface_pressure  cloudcover_total  cloudcover_low  cloudcover_mid  \
0                1008.25              57.5            64.0             0.0   
1                1008.00              78.5            86.0             0.5   
2                1007.60              83.5            86.5             0.5   
3                1007.40              71.5            72.5             0.0   
4                1007.40              49.0            49.5             0.0   
...                  ...               ...             ...             ...   
106920           1004.66              61.0             1.8            95.2   
106921           1004.86              53.8             1.6            85.4   
106922           1005.02              44.8             1.4            72.6   
106923           1005.08              40.4             7.0            57.0   
106924           1005.32              52.6            17.4            61.4   

        cloudcover_high  windspeed_10m  winddirection_10m  \
0                   0.0       2.541667              340.5   
1                   2.5       2.500000              331.0   
2                  18.5       2.833333              324.0   
3                  22.0       3.388889              324.5   
4                  13.5       3.916667              332.0   
...                 ...            ...                ...   
106920              8.4       1.938889              278.0   
106921              3.2       1.633333              211.8   
106922              0.2       1.500000              202.2   
106923              0.0       1.938889              327.2   
106924              0.0       3.261111              309.6   

        shortwave_radiation  direct_solar_radiation  diffuse_radiation  \
0                       0.0                     0.0                0.0   
1                       0.0                     0.0                0.0   
2                       0.0                     0.0                0.0   
3                       0.0                     0.0                0.0   
4                       0.0                     0.0                0.0   
...                     ...                     ...                ...   
106920                 97.0                    21.2               75.8   
106921                175.0                    52.0              123.0   
106922                326.2                   140.0              186.2   
106923                394.6                   231.8              162.8   
106924                511.6                   289.6              222.0   

        data_block_id  county  
0                 1.0     7.0  
1                 1.0     7.0  
2                 1.0     7.0  
3                 1.0     7.0  
4                 1.0     7.0  
...               ...     ...  
106920          637.0    15.0  
106921          637.0    15.0  
106922          637.0    15.0  
106923          637.0    15.0  
106924          637.0    15.0  

[106925 rows x 18 columns]

In [69]:
df_weather_naive.describe()

datetime    temperature      dewpoint           rain  \
count               106925  106925.000000  106925.00000  106925.000000   
mean   2022-07-16 05:00:00       5.361996       1.74583       0.046804   
min    2021-09-01 00:00:00     -22.800000     -25.20000       0.000000   
25%    2022-02-07 02:00:00      -0.700000      -3.20000       0.000000   
50%    2022-07-16 05:00:00       5.060000       1.40000       0.000000   
75%    2022-12-22 08:00:00      11.100000       6.70000       0.000000   
max    2023-05-30 10:00:00      30.850000      21.80000       5.700000   
std                    NaN       8.468895       7.43575       0.187637   

            snowfall  surface_pressure  cloudcover_total  cloudcover_low  \
count  106925.000000     106925.000000     106925.000000   106925.000000   
mean        0.016353       1005.456250         62.739776       48.839904   
min         0.000000        950.000000          0.000000        0.000000   
25%         0.000000        998.150000         27.000000        4.000000   
50%         0.000000       1006.450000         76.000000       46.000000   
75%         0.000000       1013.800000        100.000000       94.500000   
max         1.680000       1045.500000        100.000000      100.000000   
std         0.072828         12.753849         37.278983       40.671586   

       cloudcover_mid  cloudcover_high  windspeed_10m  winddirection_10m  \
count   106925.000000    106925.000000  106925.000000      106925.000000   
mean        35.182357        35.844983       4.253843         198.142761   
min          0.000000         0.000000       0.000000           1.000000   
25%          0.000000         0.000000       2.750000         143.000000   
50%         18.000000        11.000000       4.041667         207.000000   
75%         73.000000        84.000000       5.472222         260.500000   
max        100.000000       100.000000      16.388889         360.000000   
std         38.134510        40.903865       1.967587          87.290281   

       shortwave_radiation  direct_solar_radiation  diffuse_radiation  \
count        106925.000000           106925.000000      106925.000000   
mean            104.068434               61.111353          42.957081   
min               0.000000                0.000000           0.000000   
25%               0.000000                0.000000           0.000000   
50%               1.000000                0.000000           1.000000   
75%             135.000000               42.000000          75.000000   
max             826.200000              711.000000         364.000000   
std             176.126698              128.270405          63.284019   

       data_block_id         county  
count  106925.000000  106925.000000  
mean      319.270638      11.142857  
min         1.000000       7.000000  
25%       160.000000       8.000000  
50%       319.000000      11.000000  
75%       478.000000      14.000000  
max       637.000000      15.000000  
std       183.730665       2.799430

In [80]:
from scipy.optimize import minimize

regressors = [
    "installed_capacity",
    "direct_solar_radiation",
    "diffuse_radiation",
    "shortwave_radiation",
    "cloudcover_total",
    "cloudcover_high",
    "cloudcover_mid",
    "cloudcover_low",
    "rain",
    "snowfall",
    "temperature",
    "windspeed_10m",
    "dewpoint"
]

parameters = {
    "C_temperature": 0.004,
    "C_cloud_total": 0.75,
    "C_cloud_direct": 0.85,
    "C_cloud_diffusive": 0.65,
    "C_rain": 0.01,
    "C_snow": 0.05,
    "Thr_snow_cov_100": 0.1,
    "C_wind": 0.005,
    "C_area": 2.0
}

bounds = {
    "C_temperature": (0.0, 0.01),
    "C_cloud_total": (0.0, 1.0),
    "C_cloud_direct": (0.0, 1.0),
    "C_cloud_diffusive": (0.0, 1.0),
    "C_rain": (0.0, 1.0),
    "C_snow": (0.0, np.inf),
    "Thr_snow_cov_100": (0.0, np.inf),
    "C_wind": (0.0, 1.0),
    "C_area": (0.0, np.inf)
}

def is_foggy(temperature, dewpoint, threshold=2.0):
    """
    Determine if it's foggy based on the closeness of temperature to dewpoint.

    Parameters:
    - temperature (float): The current air temperature.
    - dewpoint (float): The current dewpoint temperature.
    - threshold (float): The temperature difference threshold to determine fog. Default is 2.0 degrees.

    Returns:
    - bool: True if foggy conditions are likely, False otherwise.
    """
    return abs(temperature - dewpoint) < threshold

def solar_output_estimator(regressors, parameters=parameters):
    baseline_temperature=25
    baseline_efficiency = 0.17

    # rain impact factor
    rain_factor = np.maximum(0, 1 - parameters["C_rain"] * regressors["rain"])
    # snow impact factor
    snow_partial_cov_factor = np.maximum(0, 1 - parameters["C_snow"] * regressors["snowfall"])
    snow_factor = np.where(regressors["snowfall"] > parameters["Thr_snow_cov_100"], 0.0, snow_partial_cov_factor)
    #snow_factor = np.maximum(0, 1 - parameters["C_snow"] * regressors["snowfall"])
    # wind impact factor
    wind_factor = 1 + parameters["C_wind"] * regressors["windspeed_10m"]

    # adjusted total horizontal irradiance
    I_adj_total = regressors["shortwave_radiation"] * (1 - parameters["C_cloud_total"] * regressors['cloudcover_total'] / 100)
    # adjusted direct irradiance
    I_adj_direct = regressors["direct_solar_radiation"] * (1 - parameters["C_cloud_direct"] * regressors['cloudcover_high'] / 100)
    # adjusted diffusive irradiance
    I_adj_diffusive = regressors["diffuse_radiation"] * (1 - parameters["C_cloud_diffusive"] * regressors['cloudcover_low'] / 100)
    
    I_adj = I_adj_total + I_adj_direct + I_adj_diffusive

    E = I_adj / 1000

    # effect of temperature
    temperature_eff = 1 + parameters["C_temperature"] * (regressors["temperature"] - baseline_temperature)
    temperature_eff[temperature_eff < 1] = 1
    
    # total effectivity
    eta_total = baseline_efficiency * rain_factor * snow_factor * wind_factor * temperature_eff

    return parameters["C_area"] * regressors["installed_capacity"] * E * eta_total
    


def fit_solar_output_estimator(X, y: np.ndarray):

    def objective_function(params):
        params = dict(zip(parameters.keys(), params))
        preds = solar_output_estimator(regressors=X, parameters=params)
        return np.mean(np.abs(preds - y))

    # Initial guess for coefficients
    initial_guess = list(parameters.values())
    # Minimize the objective function
    result = minimize(objective_function, x0=initial_guess, bounds=list(bounds.values()), method='Nelder-Mead', options={"maxiter": 1e4})
    print(result)
    if result.success:
        return dict(zip(parameters.keys(), result.x))
    else:
        raise Exception("Optimization failed: " + result.message)

df = df_train_merged_with_client.reset_index()
X = df.loc[
    (df["county_name"]=="TARTUMAA") & 
    (df["product_name"]=="Fixed") &
    (~df["is_business"])
].copy()
X["county_name"] = X["county_name"].str.lower().str.capitalize() 
X = X.set_index(["datetime", "county_name"])
X = X.join(df_weather_naive.set_index(["datetime", "county_name"]), rsuffix="wr").dropna()

X_train = X[regressors]
y_train = X["target"]

optimal_params = fit_solar_output_estimator(X_train, y=y_train)
optimal_params

       message: Optimization terminated successfully.
       success: True
        status: 0
           fun: 26.61765618185844
             x: [ 9.679e-03  1.997e-01  2.411e-06  1.000e+00  2.265e-01
                  7.769e-04  8.561e-04  1.418e-02  2.223e+00]
           nit: 739
          nfev: 1070
 final_simplex: (array([[ 9.679e-03,  1.997e-01, ...,  1.418e-02,
                         2.223e+00],
                       [ 9.684e-03,  1.997e-01, ...,  1.419e-02,
                         2.223e+00],
                       ...,
                       [ 9.682e-03,  1.997e-01, ...,  1.419e-02,
                         2.223e+00],
                       [ 9.684e-03,  1.997e-01, ...,  1.419e-02,
                         2.223e+00]]), array([ 2.662e+01,  2.662e+01,  2.662e+01,  2.662e+01,
                        2.662e+01,  2.662e+01,  2.662e+01,  2.662e+01,
                        2.662e+01,  2.662e+01]))


{'C_temperature': 0.009678842332484193,
 'C_cloud_total': 0.19966207557763163,
 'C_cloud_direct': 2.410668072833222e-06,
 'C_cloud_diffusive': 0.9999898185775731,
 'C_rain': 0.22651708142666993,
 'C_snow': 0.0007769260658818414,
 'Thr_snow_cov_100': 0.0008561196848545111,
 'C_wind': 0.014180468860900942,
 'C_area': 2.223122802888315}

In [92]:
from plotly.subplots import make_subplots

preds = solar_output_estimator(X, optimal_params)
print(np.mean(np.abs(preds-y_train)))
fig = make_subplots(rows=4, cols=1, shared_xaxes=True)
fig.add_trace(go.Scatter(x=X.reset_index()["datetime"], y=preds, opacity=1, name="predictions"), row=1, col=1)
fig.add_trace(go.Scatter(x=X.reset_index()["datetime"], y=y_train, name="labels", opacity=0.5), row=1, col=1)
fig.add_trace(go.Scatter(x=X.reset_index()["datetime"], y=X["snowfall"], name="Snow"), row=2, col=1, )
fig.add_trace(go.Scatter(x=X.reset_index()["datetime"], y=X["temperature"], name="T"), row=3, col=1)
fig.add_trace(go.Scatter(x=X.reset_index()["datetime"], y=X["dewpoint"]-X["temperature"], name="rain"), row=4, col=1)
fig.update_layout(height=600)
fig

26.61765618185844


In [ ]:
X[regressors]

installed_capacity  direct_solar_radiation  \
datetime            county_name                                               
2021-09-03 00:00:00 Tartumaa                  384.3                     0.0   
                    Tartumaa                  384.3                     0.0   
2021-09-03 01:00:00 Tartumaa                  384.3                     0.0   
                    Tartumaa                  384.3                     0.0   
2021-09-03 02:00:00 Tartumaa                  384.3                     0.0   
...                                             ...                     ...   
2023-05-30 08:00:00 Tartumaa                 1766.1                   124.0   
2023-05-30 09:00:00 Tartumaa                 1766.1                   222.0   
                    Tartumaa                 1766.1                   222.0   
2023-05-30 10:00:00 Tartumaa                 1766.1                   206.5   
                    Tartumaa                 1766.1                   206.5   

                                 diffuse_radiation  shortwave_radiation  \
datetime            county_name                                           
2021-09-03 00:00:00 Tartumaa                   0.0                  0.0   
                    Tartumaa                   0.0                  0.0   
2021-09-03 01:00:00 Tartumaa                   0.0                  0.0   
                    Tartumaa                   0.0                  0.0   
2021-09-03 02:00:00 Tartumaa                   0.0                  0.0   
...                                            ...                  ...   
2023-05-30 08:00:00 Tartumaa                 179.0                303.0   
2023-05-30 09:00:00 Tartumaa                 183.5                405.5   
                    Tartumaa                 183.5                405.5   
2023-05-30 10:00:00 Tartumaa                 246.0                452.5   
                    Tartumaa                 246.0                452.5   

                                 cloudcover_total  cloudcover_high  \
datetime            county_name                                      
2021-09-03 00:00:00 Tartumaa                100.0              1.0   
                    Tartumaa                100.0              1.0   
2021-09-03 01:00:00 Tartumaa                100.0              5.0   
                    Tartumaa                100.0              5.0   
2021-09-03 02:00:00 Tartumaa                 93.5              0.5   
...                                           ...              ...   
2023-05-30 08:00:00 Tartumaa                 51.5              0.0   
2023-05-30 09:00:00 Tartumaa                 64.5              0.0   
                    Tartumaa                 64.5              0.0   
2023-05-30 10:00:00 Tartumaa                 52.0              0.0   
                    Tartumaa                 52.0              0.0   

                                 cloudcover_mid  cloudcover_low  rain  \
datetime            county_name                                         
2021-09-03 00:00:00 Tartumaa               95.5            85.0  0.35   
                    Tartumaa               95.5            85.0  0.35   
2021-09-03 01:00:00 Tartumaa               76.5            91.0  0.20   
                    Tartumaa               76.5            91.0  0.20   
2021-09-03 02:00:00 Tartumaa               94.5            44.0  0.10   
...                                         ...             ...   ...   
2023-05-30 08:00:00 Tartumaa               67.0            13.0  0.00   
2023-05-30 09:00:00 Tartumaa               79.0            19.0  0.00   
                    Tartumaa               79.0            19.0  0.00   
2023-05-30 10:00:00 Tartumaa               57.0            19.5  0.10   
                    Tartumaa               57.0            19.5  0.10   

                                 snowfall  temperature  windspeed_10m  
datetime            county_name                                        
2021-09-03 00:00:00 Tart

In [ ]:
X.columns

Index(['county', 'product_type', 'is_business', 'product_name', 'date',
       'target', 'is_consumption', 'row_id', 'eic_count', 'installed_capacity',
       'temperature', 'dewpoint', 'rain', 'snowfall', 'surface_pressure',
       'cloudcover_total', 'cloudcover_low', 'cloudcover_mid',
       'cloudcover_high', 'windspeed_10m', 'winddirection_10m',
       'shortwave_radiation', 'direct_solar_radiation', 'diffuse_radiation',
       'data_block_id', 'countywr'],
      dtype='object')

In [ ]:
y_train

datetime             county_name
2021-09-03 00:00:00  Tartumaa         0.000
                     Tartumaa        21.319
2021-09-03 01:00:00  Tartumaa         0.000
                     Tartumaa        17.594
2021-09-03 02:00:00  Tartumaa         0.000
                                     ...   
2023-05-30 08:00:00  Tartumaa        43.342
2023-05-30 09:00:00  Tartumaa       588.066
                     Tartumaa        31.097
2023-05-30 10:00:00  Tartumaa       780.844
                     Tartumaa        30.482
Name: target, Length: 30446, dtype: float64